# <center> Chapitre 12 : Miniprojet Crafter et Survive (Corrigé)</center>

Le but de ce projet est de construire un début de jeu de type "Craft" ou pour survivre le joueur devra construire des objets et cultiver des produits à partir de ressources de base.

## Spécifications

### Développement

Pour chaque fonction demandée, un exemple d'appel est donné. Il sert à vérifier la conformité de votre proposition.

### Cycle de jeu

Le jeu, dans cette version simple, ne comporte qu'un seul joueur dont il doit maintenir les points de vie au dessus de zéro. Il n'y a pas de déplacements explicites. La santé du joueur est décrite par des points de vie et le joueur évolue dans un monde où il peut trouver, fabriquer (*crafter*) ou consommer des items.

- Le joueur perd des points de vie à chaque tour de façon constante.
- Si le joueur dispose de vetements, d'une hutte ou d'un lit, il perd moins de points de vie.
- Si le joueur mange des tomates ou du pain, il regagne des points de vie.
- Le joueur glane (récolte) des items à chaque tour de jeu.
- Le joueur peu crafter des items à chaque tour de jeu.

## Lecture des lignes des fichiers TSV

Les fichiers utiles au paramétrage du jeu sont dans le répertoire `data`. Afin de faciliter la lecture, il faut évaluer la cellule suivante :

In [ ]:
from os import chdir
from random import randint

Tous les fichiers de ce répertoire sont au format tsv. La valeur de chaque champs est séparée de la suivante par une tabulation.

Afin de pouvoir lire de façon simple les fichiers de données, définir une fonction `decoupe_tab()` qui prend en paramètre une ligne (une chaîne de caractères) composée de tokens séparés par des tabulations (`\t`) et renvoie la liste des tokens dans un tableau.

**Attention:** Les lignes lues dans le fichier finiront toutes par un retour à la ligne (`\n`). Veiller à gérer ce point lors du développement de la fonction.

In [26]:
# ------------  CORRECTION ---------- #
def decoupe_tab(li):
    tab=[""]
    j = 0
    i = 0
    while len(li) > i :
        if  li[i] == "\t" :
            j += 1
            tab.append("")
        elif li[i] != "\n" :
             tab[j] = tab[j] + li[i]
        i += 1
    return tab

In [27]:
# ------------  TEST/EXEMPLE ---------- #
print( decoupe_tab("Bonjour\ta\ttous\n") == ['Bonjour', 'a', 'tous'] )

True


## Initialisation

Le fichier `data/ressources` contient la liste des items que l'on peut glaner ou crafter dans le jeu. Sur chaque ligne est donné le nom d'un item et sa proportion dans la distribution des ressources du monde du jeu. La somme des ressources est égale à 1000; elles sont en proportion constante et quantité illimitées (renouvelées à chaque tour).

Par exemple (cf. lignes 6 et 4 du fichier), la proportion de corde ou de bois que l'on peut trouver dans le monde du jeu est respectivement de 10/1000=1% et 200/1000=20%. 

Certains items ont une proportion de 0. Ce sont les items que l'on ne peut trouver et que l'on ne peut obtenir qu'en les craftant (fabriquant).

### Définition du tableau de glanage

On souhaite définir un tableau de glanage qui représente les ressources disponibles dans le monde. Les proportions de chaque item sont données dans le fichier `data/ressources`. Dans ce tableau de glanage, chaque item sera représenté autant de fois que spécifié dans la distribution des ressources.

D'après le fichier `data/ressources`, la somme des ressources est égale à 1000 : le tableau de glanage comportera donc 1000 cases. En accord avec les lignes 1, 2 et 4 du fichier, 2 cases contiendront la chaîne de caractères `"aiguille"`, 10 cases contiendront la chaîne de caractères `"beche"` et 200 cases contiendront la chaîne de caractères `"bois"`.

Définir une fonction `import_distrib_ressources()` qui lit les données du fichier et retourne le tableau de distribution de ressources. Le tableau retourné par la fonction sera stockée dans une variable `ressources`.

**Remarque:** La fontion `import_distrib_ressources()` utilise la fonction `decoupe_tab(li)`. Elle gère l'ouverture, la lecture et la fermeture du fichier de données. Le chemin vers le fichier est passé en paramètre.

In [ ]:
# ------------  CORRECTION ---------- #
def import_distrib_ressources(path):
    ressource = []
    f = open(path, "r")
    li = f.readline()
    while ( li != "" ) :
        item_quantite = decoupe_tab(li)
        item = item_quantite[0]
        quantite = int(item_quantite[1])
        j = 0
        while( j < quantite):
            ressource.append(item)
            j += 1
        li = f.readline()
    f.close()
    return ressource

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
ressources = import_distrib_ressources("data/ressources")
print(len(ressources))
print(ressources[500] == "osier")

### Création du coffre

Définir une fonction `init_coffre()` qui construit et initialise un `coffre`. Le `coffre` prend la forme d'un dictionnaire où
- les clefs sont les noms des items
- les valeurs sont le nombre d'items en possession du joueur.
Au départ le coffre est vide. La liste des clefs est lue dans le fichier `data/ressources`.

**Remarque:** Cette fonction est assez similaire à la précédente.

In [ ]:
# ------------  CORRECTION ---------- #
def init_coffre(path):
    coffre = dict()
    f = open(path, "r")
    li = f.readline()
    while ( li != "" ) :
        item_proba = decoupe_tab(li)
        coffre[item_proba[0]] = 0
        li = f.readline()
    f.close()
    return coffre

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
coffre = init_coffre("data/ressources")
print( coffre)

## Gestion du coffre

Dans ce jeu, la taille du coffre est infinie, *i.e*, si le nombre de clefs est fixé par le nombre d'items, le nombre d'items que l'on peut avoir dans le coffre est illimité...

### Représentation du coffre

Afin de pouvoir représenter le contenu du tableau de façon élégante, on veut pouvoir afficher à l'écran des chaînes de caractère de longueur différentes sur un même nombre de caractères. Définir une fonction `fixe_longueur()` qui prend en paramètres une chaîne de caractère et une longueur entière et qui retourne la chaine de caractère en lui ayant ajouté à gauche autant de caractères espace que nécessaire pour que sa longueur soit celle passé en paramètre.
Si la longueur de la chaine de départ est plus longue que la longueur de la chaine souhaitée alors la fonction ne fait rien et retourne la chaine initiale.

In [ ]:
# ------------  CORRECTION ---------- #
def fixe_longueur( chaine, longueur ):
    chaine_retour = chaine
    if( len(chaine)<longueur) :
        i = len(chaine)
        while ( i < longueur ):
            chaine_retour = " " + chaine_retour
            i += 1
    return chaine_retour

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
print( "->" + fixe_longueur( "1234", 2) + "<-")
print( "->" + fixe_longueur( "1234", 4) + "<-")
print( "->" + fixe_longueur( "1234", 6) + "<-")
print( "->" + fixe_longueur( "1234", 8) + "<-")

Définir une fonction `liste_items()` qui renvoie la liste des items d'un coffre, *i.e.*, la liste des clefs d'un dictionnaire. La fonction prend en paramètre un dictionnaire (un coffre) et retourne la liste des noms des items du coffre (la liste des clefs du dictionnaire).

In [ ]:
# ------------  CORRECTION ---------- #
def liste_items(coffre ):
    return(list(dict.keys(coffre)))

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
print(liste_items({1:"a", 2:"b", "tutu":"TOTO"}))
print("---------------------")
print(liste_items(coffre ))

Définir une fonction `ouvre_coffre()` qui permet d'afficher de façon formatée le contenu du coffre. La fonction prend en paramètre un coffre (un dictionnaire), ne renvoie rien mais affiche un tableau comportant deux colonnes:
    - une colonne pour les clefs (les items) et
    - une colonne pour les valeurs (les quantités) d'items
et autant de lignes qu'il y a de couples (clef:valeur) dans le coffre.

**Remarque:** Il faut utiliser les fonctions `fixe_longueur()` et `liste_items()`

In [ ]:
# ------------  CORRECTION ---------- #
def ouvre_coffre( coffre ):
    items = liste_items(coffre )
    i = 0
    while( i < len(items )) :
        print( fixe_longueur(items[i], 15) +
              " | " +
              fixe_longueur(str(coffre[items[i]]), 5) )
        i += 1

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
ouvre_coffre( coffre )

### Ajouter d'un item au coffre

Définir une fonction `ajoute()` qui prend en paramètre un coffre et le nom d'un item et ajoute cet item au coffre (augmente la quantité de cet item de +1).

In [ ]:
# ------------  CORRECTION ---------- #
def ajoute(coffre, item):
    coffre[item] += 1

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
print( coffre["aiguille"])
ajoute(coffre, "aiguille")
print( coffre["aiguille"])

### Ajout au panier des objets glanés

Définir une fonction `ajoute_plusieurs()` qui prend en paramètre un coffre et une liste d'items (glanés) et les ajoute au coffre.

**Remarque:** Utiliser et généraliser la fonction `ajoute()` définie supra.

In [ ]:
# ------------  CORRECTION ---------- #
def ajoute_plusieurs( coffre, panier ) :
    i = 0
    while( i < len(panier)):
        ajoute(coffre, panier[i])
        i += 1

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
print(coffre["aiguille"])
print(coffre["beche"])
ajoute_plusieurs(coffre, ["aiguille","beche","aiguille"])
print(coffre["aiguille"])
print(coffre["beche"])

### Tester la présence d'un item dans le coffre

Définir une fonction `est_present()` qui teste la présence en quantité superieure ou égale à 1 d'un item dans le coffre. La fonction prend en paramètre un coffre, le nom d'un item et retourne `True` si il y a au moins un item de ce type dans le coffre et `False` sinon.

In [ ]:
# ------------  CORRECTION ---------- #
def est_present( coffre, item):
    return coffre[item] > 0

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
print(coffre["aiguille"])
print(est_present(coffre, "aiguille"))
print(coffre["hutte"])
print(est_present(coffre, "hutte"))

### Tester la présence d'une liste item dans le coffre

Définir une fonction `sont_presents()` qui teste la présence de plusieurs items dans le coffre. La fonction prend en paramètre un coffre, un tableau d'items et retourne `True` si tous les items du tableau sont présents dans le coffre et `False` sinon.

**Remarque:** Il faut utiliser la fonction `est_present()`

In [ ]:
# ------------  CORRECTION ---------- #
def sont_presents( coffre, liste_item):
    i = 0
    while( i<len(liste_item) and est_present( coffre, liste_item[i])):
        i += 1
    return(i==len(liste_item))

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
ajoute_plusieurs(coffre,["bois","fer"])
print(sont_presents( coffre, ["bois","fer"]))
print(sont_presents( coffre, ["bois","fer","hutte"]))

### Retirer un item du coffre

Définir une fonction `retire()` qui prend en paramètre un coffre et le nom d'un item. Si le coffre contient l'item, la quantité de cet item est décrémentée dans le coffre et la fonction renvoie `True`, sinon la quantité de cet item n'est pas décrémentée dans le coffre et la fonction renvoie `False`.

**Attention:** Il faut utiliser la fonction `est_present()`

In [ ]:
# ------------  CORRECTION ---------- #
def retire( coffre, item):
    ok = est_present( coffre, item)
    if ( ok ):
        coffre[item] -= 1
    return( ok )

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
print( coffre["aiguille"])
retire(coffre, "aiguille")
print( coffre["aiguille"])

### Retirer une liste d'items du coffre

Définir une fonction `retire_plusieurs()` qui prend en paramètre un coffre et un tableau d'items à retirer du coffre.
- Si tous les items du tableau sont présents dans le coffre la quantité de chacun est décrémentée de 1 et la fonction retourne `True`. Si il manque au moins 1 item du tableau dans le coffre la fonction ne modifie pas le contenu du coffre et renvoie `False`.

**Attention:** Il faut utiliser les fonctions `sont_presents()` et `retire()`

In [ ]:
# ------------  CORRECTION ---------- #
def retire_plusieurs( coffre, liste_item):
    ok = sont_presents(coffre, liste_item)
    if ( ok ):
        i = 0
        while( i<len(liste_item)):
            retire( coffre, liste_item[i])
            i += 1
    return( ok )

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
print( coffre["aiguille"])
print( coffre["bois"])
retire_plusieurs(coffre, ["aiguille","bois"])
print( coffre["aiguille"])
print( coffre["bois"])

## Glanage

A chaque tour de jeu, le joueur reçoit 5 items qu'il a glanés (trouvés et ramassés) durant le tour précédent.  Les items trouvés suivent la distribution des ressources du monde du jeu qui est  décrite dans le tableau `ressources` définit supra.

### Tirage des items glanés

Définir une fonction `glaner()` qui prend en paramètre le tableau de ressources et retourne un tableau des objets glanés. Pour  cela, tirer 5 fois un entier `i` compris entre 0 et la taille du tableau de ressources et renvoyer dans le tableau les noms des 5 items trouvés aux positions `i`.

In [34]:
# ------------  CORRECTION ---------- #
def glaner(ressources):
    panier = []
    i = 0
    while( i < 5 ):
        panier.append(ressources[randint( 0, len(ressources)-1)])
        i += 1
    return(panier)

In [35]:
# ------------  TEST/EXEMPLE ---------- #
# Attention: fonction aleatoire, le     #
# resultat peut être différent          #
glaner(ressources)

['fer', 'osier', 'coton', 'graine_ble', 'paille']

### Tirage des items glanés (suite)

Modifier la fonction précédente pour que le nombre d'items glanés soit un paramètre de la fonction

In [36]:
# ------------  CORRECTION ---------- #
def glaner(ressources, quantite):
    panier = []
    i = 0
    while( i < quantite ):
        panier.append(ressources[randint( 0, len(ressources)-1)])
        i += 1
    return(panier)

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
print( len(glaner(ressources,   2)) ==   2 )
print( len(glaner(ressources, 500)) == 500 )

## Craft

Les règles de *craft* définissent les objets nécessaires à la fabrication d'autres objets. Ces règles sont détaillées dans le fichier `data/regles_craft`. Le format de ce fichier est le suivant:
- la première colonne donne le type/nom de l'objet à fabriquer
- les colonnes suivantes donnent les noms/types des items nécessaires à la fabrication

Par exemple :
- pour fabriquer 1 item *panier* il faut 1 item *osier*
- pour fabriquer 1 items *ble* il faut 1 item *graine_ble* et 1 item *beche*

### Initialisation du dictionnaire des règles de craft

Afin de stocker les règles de craft, on utilise un dictionnaire où 
- les clefs sont les objets à fabriquer
- les valeurs sont un tableau contenant la liste des items nécessaires à sa fabrication

Définir une fonction `import_regles_craft()` qui lit les données du fichier et retourne le dictionnaire des règles de craft. Le dictionnaire retourné par la fonction sera stocké dans une variable `règles_craft`.

**Remarque:** La fontion `import_regles_craft()` utilise la fonction `decoupe_tab(li)`. Elle gère l'ouverture, la lecture et la fermeture du fichier de données. Le chemin vers le fichier est passé en paramètre.

In [ ]:
# ------------  CORRECTION ---------- #
def import_regles_craft(path):
    regles_craft = dict()
    f = open( path, 'r')
    li = f.readline()
    while ( li != "" ) :
        buf = decoupe_tab(li)
        regles_craft[ buf[0] ] = buf[1:]
        li = f.readline()
    f.close()
    return regles_craft

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
regles_craft = import_regles_craft("data/regles_craft")
print(regles_craft["pain"] == ["ble", "bois"])
print(regles_craft["hutte"] == ["osier", "bois", "clou", "marteau"] )

### Tester si on peut crafter un item

Avant de crafter un item, on a besoin de comparer le stock d'items dans le coffre à la règle de craft pour s'assurer que l'on dispose de tous les items nécessaires à la fabrication.

Définir une fonction `craft_possible()` qui prend en paramètres un coffre, un dictionnaire de règles de craft et le nom d'un item à crafter et retourne le booléen `True` si les items nécessaires au craft sont disponibles dans le coffre et `False` sinon.

**Attention:** Vous devez utiliser la fonction `sont_presents()`

In [ ]:
# ------------  CORRECTION ---------- #
def craft_possible(coffre, regles_craft, item) :
    return sont_presents(coffre, regles_craft[item])

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
coffre = init_coffre("data/ressources")
ajoute_plusieurs(coffre, ["fer","bois"])
print(craft_possible(coffre, regles_craft, "beche"))
print(craft_possible(coffre, regles_craft, "pain"))

### Crafter

Définir une fonction `craft()` qui prend en paramètres un coffre, les règles de craft et le nom d'un item et si le craft de l'item indiqué est possible, décrémente le coffre des items utilisés pour la fabrication et incrémente le coffre de l'item crafté. La fonction renvoie `True` si le craft a eu lieu et `False` sinon.

In [ ]:
# ------------  CORRECTION ---------- #
def craft(coffre, regles_craft, item):
    possible = craft_possible(coffre, regles_craft, item)
    if ( possible ):
        retire_plusieurs( coffre, regles_craft[item])
    return possible

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
coffre = init_coffre("data/ressources")
ajoute_plusieurs(coffre, ["fer","bois"])
print(coffre["fer"])
print(coffre["bois"])
print(coffre["beche"])
print(craft(coffre,regles_craft,"beche"))
print(coffre["fer"])
print(coffre["bois"])
print(coffre["beche"])

### Manger

Les items mangeables sont les suivants: `"pain"`, `"tomate"` ou `"ble"`. Ils rapportent respectivement 10, 5 et 1 point de vie.

Définir une fonction `manger()` qui prend en paramètres un coffre, un nom d'item et un niveau de point de vie. Si l'item est un des 3 items mangeable et que l'item est présent dans le coffre, alors la fonction retourne le nombre de points de vie augmenté du gain défini supra et décrémente le coffre de l'item consommé. Si l'item n'est pas mangeable ou s'il n'est pas disponible dans le coffre, la fonction affiche un message d'erreur et retourne la valeur des points de vie inchangée.

**Attention**: Il faut utiliser les fonctions `retire()`et `est_present()`.

In [ ]:
# ------------  CORRECTION ---------- #
def manger(coffre, item, PdV):
    est_comestible = ( item == "pain" or item == "tomate" or item == "ble" )
    if( est_comestible and est_present(coffre, item) ):
        retire(coffre, item)
        if ( item == "pain" ) :
            return( PdV + 10 )
        elif ( item == "tomate" ) :
            return( PdV + 5 )
        else :
            return( PdV + 1 )
    elif ( not( est_comestible ) ) :
        print("Erreur : l'item " + item + " n'est pas comestible !")
        return(PdV)
    else :
        print("Erreur : l'item " + item + " n'est pas présent dans votre coffre !")
        return(PdV)

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
coffre = init_coffre("data/ressources")
ajoute_plusieurs(coffre, ["fer","pain"])
PdV = 1000
print( manger(coffre, "pain", PdV) )
print( manger(coffre, "fer", PdV) )
print( manger(coffre, "tomate", PdV) )

### Point de vie

A chaque tour, les points de vie du joueur sont recalculés. Par défaut, il sont décrémentés de 50. Cependant, si le coffre contient un vêtement, un lit ou une hutte, alors ils décroissent moins:
- la possession d'au moins un vêtement diminue de 5 le décrément
- la possession d'au moins un lit diminue de 7 le décrément
- la possession d'au moins une hutte diminue de 15 le décrément
Définir une fonction `maj_PdV()` qui prend en paramètres un coffre et la valeur des point de vie avant décrément de tour et retourne la valeur des points de vie après le décrément en tenant compte du contenu du coffre.

**Attention:** Il faut utiliser la fonction `est_present()`.

In [ ]:
# ------------  CORRECTION ---------- #
def maj_PdV(coffre, pdv) :
    decrement = 50
    if ( est_present(coffre,"vetement")) :
        decrement -= 5
    if ( est_present(coffre,"lit")) :
        decrement -= 7
    if ( est_present(coffre,"hutte")) :
        decrement -= 15
    return( pdv - decrement)

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
coffre = init_coffre("data/ressources")
print(maj_PdV(coffre, 100) == 50)
ajoute( coffre, "vetement")
print(maj_PdV(coffre, 100) == 55) # avec un vetement
ajoute( coffre, "lit")
print(maj_PdV(coffre, 100) == 62) # avec un vetement et un lit
ajoute( coffre, "hutte")
print(maj_PdV(coffre, 100) == 77) # avec un vetement, un lit et une hutte

## Menu et tours de jeu
### Test d'appartenance à une liste

Définir une fonction `est_dans()` qui prend en paramètres une chaine de caractère et un tableau de chaines de caractères et renvoie `True` si la chaine est présente dans le tableau et `False` sinon.

In [ ]:
# ------------  CORRECTION ---------- #
def est_dans( chaine, liste_de_chaine ):
    i = 0
    while( ( i < len(liste_de_chaine) ) and ( chaine != liste_de_chaine[i] ) ) :
        i += 1
    return( i != len(liste_de_chaine))

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
print(est_dans( "Hello", ["Bonjour", "a", "tous"] ))
print(est_dans( "Bonjour", ["Bonjour", "a", "tous"] ))

### Saisie controlée

Définir une fonction `saisie_controlee()` qui prend en paramètres un message d'invite et une liste de valeurs admissibles à la saisie. La fonction répète la demande de la saisie au clavier tant que l'utilisateur n'a pas saisi une valeur présente dans la liste des valeurs admissibles et retourne la première valeur admissible saisie par l'utilisateur.

**Attention** : Il faut utiliser la fonctiona `est_dans()`.

In [ ]:
# ------------  CORRECTION ---------- #
def saisie_controlee( message, admissible) :
    print(message)
    saisie = input()
    while( not(est_dans( saisie, admissible) ) ):
        print("Saisie non reconnue")
        print(message)
        saisie = input()
    return(saisie)

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
saisie_controlee( "Tapez [y,n]", ["y","n"])

### Choix d'un item

Définir une fonction de saisie controlée `choix_item()` qui permet de choisir le nom d'un item d'un coffre (*i.e.*, une clef parmi les clefs d'un dictionnaire). La fonction prend en paramètre un coffre et retourne le nom d'un item du coffre.

**Attention** : Il faut utiliser les fonctions `saisie_controlee()` et `liste_items(coffre )`.

In [ ]:
# ------------  CORRECTION ---------- #
def choix_item(coffre) :
    return(saisie_controlee( "Saisissez le nom d'un item", liste_items(coffre ) ))

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
choix_item(coffre)

## Définition du menu de tour

Définir la fonction `partie()` permettant de jouer...

In [ ]:
import sys
# ------------  CORRECTION ---------- #
def partie():
    print("Craft and Survive")
    # Initialisation 
    ressources = import_distrib_ressources("data/ressources")
    coffre = init_coffre("data/ressources")
    regles_craft = import_regles_craft("data/regles_craft")
    pdV = 1000
    tour_sup = True
    while( tour_sup and pdV > 0 ) :
        ajoute_plusieurs(coffre,glaner(ressources,5))
        print("---------------------\nVotre coffre :")
        ouvre_coffre(coffre)
        print("---------------------\nVos PdV : " + str( pdV))
        choix = saisie_controlee( "Souhaitez vous crafter?", ["oui","non"])
        if( choix == "oui" ) :
            print( "la liste des items est:" )
            print(liste_items(coffre ))
            choix = saisie_controlee( "Que souhaitez vous crafter?",liste_items(coffre ))
            craft(coffre, regles_craft, choix)
        choix = saisie_controlee( "Souhaitez vous manger?", ["oui","non"])
        if( choix == "oui" ) :
            choix = saisie_controlee( "Que souhaitez vous manger? (ble, pain, tomate)",["ble", "pain", "tomate"])
            pdV = manger(coffre, choix, pdV)
        tour_sup = ( saisie_controlee( "Souhaitez vous continuer?", ["oui","non"]) == "oui" )

In [ ]:
# ------------  TEST/EXEMPLE ---------- #
partie()

## Pistes pour aller plus loin

- afficher les règles de craft
- définir des règles de gain de points de vie quand on mange pain ou tomate
- Pour rendre le jeu plus intéressant, on peut tirer aléatoirement le nombre d'items glanés à chaque tour. Par exemple, on peut se donner comme règle que le nombre d'items glanés varie de façon uniforme entre 0 et 5. On peut utiliser une distribution non uniforme sur le nombre d'items trouvés à chaque tour
- Les règles données dans le fichier `data/regles_craft_plus` sont plus évoluées que les précédentes. Celles-ci définissent les quantités et type d'objets nécessaires pour en fabriquer d'autres. Le format de ce fichier est le suivant:
- la première colonne donne le type/nom de l'objet à fabriquer
- la deuxième colonne donne la quantité produite lors de la fabrication
- les colonnes suivantes donnent les noms/types et quantités nécessaires à la fabrication

Par exemple :
- pour fabriquer 1 item `panier` il faut 10 items `osier`
- pour fabriquer 10 items `ble` il faut 1000 items `graine_ble` et 1 item `beche`

Afin d'utiliser ces règles de craft, il faut :
- modifier la structure du dictionnaire des règles de craft
- modifier la fonction de lecture/initialisation des règles
- modifier la fonction qui teste s'il y a suffisament d'éléments pour en crafter un autre
- modifier la fonction de craft qui supprime les éléments utilisés dans la fabrication et ajoute les éléments craftés.